In [97]:
!pip install plotly

In [98]:
import warnings
warnings.filterwarnings('ignore')

In [99]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats
import plotly.express as px
import plotly.io as pio

In [100]:
pio.templates.default = "plotly_white" 
custom_palette = px.colors.qualitative.Vivid
custom_continuous_scale = px.colors.sequential.Plasma

### EDA

Так как намайненные данные о фильмах носят больше описательный характер, возьмём датасет растворимостей BigSolDB (это датасет для исследования, так что обязательно нужно проводить EDA)

BigSolDB v.2.0 contains 103944 experimentally measured solubility values of 1448 organic compounds in 213 solvents reported in the 1595 literature peer-reviewed articles

The 12 columns of this dataset are explained as follows:

SMILES_Solute — SMILES representation of the solute molecule  
Temperature_K — temperature for the reported solubility value, K  
Solvent — solvent name  
SMILES_Solvent — SMILES representation of the solvent molecule  
Solubility(mole_fraction) — the reported solubility value expressed in mole fraction of solute  
Solubility(mol/L) — the recalculated solubility value expressed in molar concentration of solute (mol/L)  
LogS(mol/L) — decimal logarithm of the recalculated solubility value expressed in molar concentration of solute (mol/L)  
Compound_Name — solute name  
CAS — solute CAS number  
PubChem_CID — solute PubChem_CID  
FDA_Approved — designation if the solute is a FDA approved drug. ‘Yes’ is stated for FDA approved drugs while ‘No’ is stated for others.  
Source — DOI of a data source for given values  
An addition dataset of solvents densities values is also presented.  

The 4 columns of this dataset are explained as follows:  

Solvent — solvent name  
Temperature_K — temperature for the reported density value, K  
Density_g/cm^3 – the reported density value  
Source — data source for given values  
An additional note - the values in columns 'Solubility(mol/L)' and 'LogS(mol/L)' were recalculated from the mole fraction values reported in the source articles ('Solubility(mole_fraction)' column), using the densitites of solvents expressed in BigSolDBv2.0_densities.csv.  

### Предварительный обзор

In [101]:
url = "https://zenodo.org/records/15094979/files/BigSolDBv2.0.csv?download=1"
df = pd.read_csv(url)

In [102]:
%matplotlib inline
sns.set(style="whitegrid")
pd.set_option("display.max_columns", 50)
pd.set_option("display.max_rows", 100)
pd.set_option("display.float_format", lambda x: f"{x:.4f}")

Общая сводка по данным

In [103]:
print("Shape:", df.shape)

Shape: (103944, 12)


In [104]:
print("Columns:", df.columns.tolist())

Columns: ['SMILES_Solute', 'Temperature_K', 'Solvent', 'SMILES_Solvent', 'Solubility(mole_fraction)', 'Solubility(mol/L)', 'LogS(mol/L)', 'Compound_Name', 'CAS', 'PubChem_CID', 'FDA_Approved', 'Source']


In [105]:
df.head()

SMILES_Solute  Temperature_K  Solvent SMILES_Solvent  \
0  CCCCCCCCCCCCCCCCCCCC(=O)OCCO       311.2500  ethanol            CCO   
1  CCCCCCCCCCCCCCCCCCCC(=O)OCCO       314.6500  ethanol            CCO   
2  CCCCCCCCCCCCCCCCCCCC(=O)OCCO       319.1500  ethanol            CCO   
3  CCCCCCCCCCCCCCCCCCCC(=O)OCCO       322.1500  ethanol            CCO   
4  CCCCCCCCCCCCCCCCCCCC(=O)OCCO       324.1500  ethanol            CCO   

   Solubility(mole_fraction)  Solubility(mol/L)  LogS(mol/L)  \
0                     0.0006             0.0101      -1.9964   
1                     0.0012             0.0201      -1.6968   
2                     0.0020             0.0334      -1.4768   
3                     0.0050             0.0834      -1.0791   
4                     0.0139             0.2333      -0.6321   

                  Compound_Name         CAS  PubChem_CID FDA_Approved  \
0  Ethylene glycol monoeicosate  26158-80-5  538813.0000           No   
1  Ethylene glycol monoeicosate  26158-80-5  538813.0000           No   
2  Ethylene glycol monoeicosate  26158-80-5  538813.0000           No   
3  Ethylene glycol monoeicosate  26158-80-5  538813.0000           No   
4  Ethylene glycol monoeicosate  26158-80-5  538813.0000           No   

               Source  
0  10.1007/bf00649573  
1  10.1007/bf00649573  
2  10.1007/bf00649573  
3  10.1007/bf00649573  
4  10.1007/bf00649573

Проведём обзор данных: типы, базовая статистика, пропуски

In [106]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 103944 entries, 0 to 103943
Data columns (total 12 columns):
 #   Column                     Non-Null Count   Dtype  
---  ------                     --------------   -----  
 0   SMILES_Solute              103944 non-null  object 
 1   Temperature_K              103944 non-null  float64
 2   Solvent                    103944 non-null  object 
 3   SMILES_Solvent             103944 non-null  object 
 4   Solubility(mole_fraction)  103944 non-null  float64
 5   Solubility(mol/L)          100983 non-null  float64
 6   LogS(mol/L)                100983 non-null  float64
 7   Compound_Name              103944 non-null  object 
 8   CAS                        96488 non-null   object 
 9   PubChem_CID                101351 non-null  float64
 10  FDA_Approved               103944 non-null  object 
 11  Source                     103944 non-null  object 
dtypes: float64(5), object(7)
memory usage: 9.5+ MB


PubChem_CID это ID, а не числовая характеристика, так что лучше преобразовать в строку, чтобы оно не анализировалось как число

In [107]:
if "PubChem_CID" in df.columns:
    df["PubChem_CID"] = df["PubChem_CID"].astype(str)

### Пропуски - completeness

Больше всего пропусков приходится на в целом таргетные данные Solulubility и LogS растворимости. Также порядка 7% пропусков приходится на CAS

In [108]:
missing = df.isnull().sum().sort_values(ascending=False)
print("Missing values per column:", missing)

Missing values per column: CAS                          7456
Solubility(mol/L)            2961
LogS(mol/L)                  2961
SMILES_Solute                   0
Temperature_K                   0
Solvent                         0
SMILES_Solvent                  0
Solubility(mole_fraction)       0
Compound_Name                   0
PubChem_CID                     0
FDA_Approved                    0
Source                          0
dtype: int64


Доля пропусков

missing_frac = (df.isnull().sum() / len(df)).sort_values(ascending=False)
print("Missing fractions per column:", missing_frac)

### Первичный анализ и распределения значений

Температуры распределены нормальным образом, как и LogS значений растворимости 

In [109]:
num_cols = df.select_dtypes(include=[np.number]).columns.tolist()
print("Numerical columns:", num_cols)

for col in num_cols:
    fig = px.histogram(
        df,
        x=col,
        nbins=50,
        marginal="box",
        title=f"Distribution of {col}"
    )
    fig.show()

Numerical columns: ['Temperature_K', 'Solubility(mole_fraction)', 'Solubility(mol/L)', 'LogS(mol/L)']


### Корреляция числовых признаков

Забавно, что Solulubility mole_fraction и Solulubility mol/L, как и LogS не скоррелированы на единичку. То есть формулы перевода не линейные, это логично и правильно :)) 

In [110]:
corr = df[num_cols].corr()
fig = px.imshow(corr, text_auto='.2f', title='Correlation matrix')
fig.update_layout(width=800, height=700)
fig.show()

### Уникальные значения - uniqueness

Видим, что достаточно много SMILES формул, которые соответствуют записям в датасете с различными температурами. Также видно, что этанол выступает самым частым растворителем

Полные дубликаты строк:

In [111]:
total_duplicates = df.duplicated().sum()
print(f"Количество полных дублей строк в датасете: {total_duplicates}")

Количество полных дублей строк в датасете: 0


Проверим дубли по химическому представлению соединения растворяемого вещества (SMILES_Solvent):

In [112]:
if "SMILES_Solvent" in df.columns:
    smiles_duplicates = df["SMILES_Solvent"].duplicated().sum()
    unique_smiles = df["SMILES_Solvent"].nunique()
    total_smiles = len(df["SMILES_Solvent"])
    print(f"Дубликатов по SMILES: {smiles_duplicates}")
    print(f"Уникальных SMILES: {unique_smiles} из {total_smiles} записей")
    
    # Если нужно — выведем примеры дублей
    duplicated_smiles = df[df["SMILES_Solvent"].duplicated(keep=False)].sort_values("SMILES_Solvent")
    print(f"Примеры дублей SMILES:")
    display(duplicated_smiles.head(10))

Дубликатов по SMILES: 103735
Уникальных SMILES: 209 из 103944 записей
Примеры дублей SMILES:


SMILES_Solute  Temperature_K  \
97654  O=C(NC(Cc1cc(=O)[nH]c2ccccc12)C(=O)O)c1ccc(Cl)cc1       298.1500   
97650  C=CC(=O)Nc1cc(Nc2nccc(-c3cn(C)c4ccccc34)n2)c(O...       313.2000   
97651  C=CC(=O)Nc1cc(Nc2nccc(-c3cn(C)c4ccccc34)n2)c(O...       318.2000   
97652  O=C(NC(Cc1cc(=O)[nH]c2ccccc12)C(=O)O)c1ccc(Cl)cc1       288.1500   
97653  O=C(NC(Cc1cc(=O)[nH]c2ccccc12)C(=O)O)c1ccc(Cl)cc1       293.1500   
97581  CN(Cc1ccccc1)CN1C(=O)C(=NNC(=O)c2ccccc2OCc2ccc...       318.1500   
97655  O=C(NC(Cc1cc(=O)[nH]c2ccccc12)C(=O)O)c1ccc(Cl)cc1       303.1500   
97656  O=C(NC(Cc1cc(=O)[nH]c2ccccc12)C(=O)O)c1ccc(Cl)cc1       308.1500   
97649  C=CC(=O)Nc1cc(Nc2nccc(-c3cn(C)c4ccccc34)n2)c(O...       308.2000   
97657        COc1ccccc1OCCNCC(O)COc1cccc2[nH]c3ccccc3c12       288.1500   

       Solvent SMILES_Solvent  Solubility(mole_fraction)  Solubility(mol/L)  \
97654  PEG-400              -                     0.0026                NaN   
97650  PEG-400              -                     0.0058                NaN   
97651  PEG-400              -                     0.0073                NaN   
97652  PEG-400              -                     0.0024                NaN   
97653  PEG-400              -                     0.0025                NaN   
97581  PEG-400              -                     0.0114                NaN   
97655  PEG-400              -                     0.0028                NaN   
97656  PEG-400              -                     0.0029                NaN   
97649  PEG-400              -                     0.0042                NaN   
97657  PEG-400              -                     0.0501                NaN   

       LogS(mol/L)                                      Compound_Name  \
97654          NaN                                         Rebamipide   
97650          NaN                                        Osimertinib   
97651          NaN                                        Osimertinib   
97652          NaN                                         Rebamipide   
97653          NaN                                         Rebamipide   
97581          NaN  N′-(1-(n-(methyl) benzylaminomethyl)-2-oxoindo...   
97655          NaN                                         Rebamipide   
97656          NaN                                         Rebamipide   
97649          NaN                                        Osimertinib   
97657          NaN                                         Carvedilol   

                CAS  PubChem_CID FDA_Approved                        Source  
97654    90098-04-7       5042.0           No  10.1016/j.molliq.2019.111041  
97650  1421373-65-0   71496458.0          Yes  10.1016/j.molliq.2019.03.128  
97651  1421373-65-0   71496458.0          Yes  10.1016/j.molliq.2019.03.128  
97652    90098-04-7       5042.0           No  10.1016/j.molliq.2019.111041  
97653    90098-04-7       5042.0           No  10.1016/j.molliq.2019.111041  
97581  1884472-26-7  137175079.0           No  10.1016/j.molliq.2016.04.068  
97655    90098-04-7       5042.0           No  10.1016/j.molliq.2019.111041  
97656    90098-04-7       5042.0           No  10.1016/j.molliq.2019.111041  
97649  1421373-65-0   71496458.0          Yes  10.1016/j.molliq.2019.03.128  
97657    72956-09-3       2585.0          Yes  10.1016/j.molliq.2019.111622

In [113]:
cat_cols = df.select_dtypes(include=["object", "category"]).columns.tolist()

for col in cat_cols:
    print("Уникальные:", df[col].nunique())
    print("Топ-10 частых значений:")
    print(df[col].value_counts().head(10))
    print()

Уникальные: 1448
Топ-10 частых значений:
SMILES_Solute
CN1CCN(C2=Nc3cc(Cl)ccc3Nc3ccccc32)CC1                                                                   416
C[C@@H]1CC[C@@]2(OC1)O[C@H]1C[C@H]3[C@@H]4CC=C5C[C@@H](O)CC[C@]5(C)[C@H]4CC[C@]3(C)[C@H]1[C@@H]2C       380
Cn1c(=O)c2c(ncn2CC2OCCO2)n(C)c1=O                                                                       357
CC(=O)Nc1ccc(OC(=O)c2ccccc2OC(C)=O)cc1                                                                  313
O=C(O)c1ccccc1                                                                                          311
O=[N+]([O-])N1C2C3N([N+](=O)[O-])C1C1N([N+](=O)[O-])C(C(N1[N+](=O)[O-])N3[N+](=O)[O-])N2[N+](=O)[O-]    295
CC(C)C(=O)Nc1ccc([N+](=O)[O-])c(C(F)(F)F)c1                                                             272
Nc1ccc(S(N)(=O)=O)cc1                                                                                   267
O=c1[nH]cc(F)c(=O)[nH]1                                                          

In [114]:
for col in cat_cols:
    if df[col].nunique() < 20:
        fig = px.bar(df[col].value_counts().head(15).reset_index(), 
                     x='count', 
                     y=col,
                     title=f"Counts of {col}",
                     orientation='h')
        fig.update_layout(height=400, width=600)
        fig.show()

### Оценка выбросов

В целом, немного странно, что количество выбросов по разным шкалам отличается, хотя у mole_fraction и mol_L должно быть приблизительно одинаковым. А вот с LogS будто бы можно понять, потому что шкала логарифмическая?

In [115]:
def detect_outliers_iqr(data, col, k=1.5):
    q1 = data[col].quantile(0.25)
    q3 = data[col].quantile(0.75)
    iqr = q3 - q1
    lower, upper = q1 - k*iqr, q3 + k*iqr
    return data[(data[col] < lower) | (data[col] > upper)]

print("Количество выбросов по числовым признакам:")
for col in num_cols:
    outliers = detect_outliers_iqr(df, col)
    print(f"{col}: выбросов = {len(outliers)} ({len(outliers)/len(df)*100:.2f}%)")

Количество выбросов по числовым признакам:
Temperature_K: выбросов = 1147 (1.10%)
Solubility(mole_fraction): выбросов = 14026 (13.49%)
Solubility(mol/L): выбросов = 14592 (14.04%)
LogS(mol/L): выбросов = 1544 (1.49%)


### Обработка пропусков

Числовые значения можем заполнять медианой

In [116]:
threshold = 0.05
cols_to_drop = missing_frac[missing_frac > threshold].index.tolist()
print("Columns to drop (too many missing):", cols_to_drop)

df2 = df.drop(columns=cols_to_drop)

for col in num_cols:
    if col in df2.columns:
        if df2[col].isnull().any():
            median_val = df2[col].median()
            df2[col].fillna(median_val, inplace=True)

Columns to drop (too many missing): ['CAS']


Для категориальных можно заполнить модой или “Unknown”

In [117]:
for col in cat_cols:
    if col in df2.columns:
        if df2[col].isnull().any():
            mode_val = df2[col].mode().iloc[0]
            df2[col].fillna(mode_val, inplace=True)

### Анализ групп

Растворители и растворяемые вещества - распределения величин

In [118]:
sol_col = "Solubility(mol/L)"

if {"SMILES_Solvent", sol_col}.issubset(df.columns):
    stats_by_solvent = (
        df.groupby("Solvent")[sol_col]
        .agg(
            count="count",
            n_unique=lambda x: x.nunique(),
            mean="mean",
            median="median",
            std="std",
            min="min",
            max="max"
        )
        .sort_values("count", ascending=False)
    )

    print("Статистика по растворителям (Solvent):")
    display(stats_by_solvent.head(20))

else:
    print(f"Не найдены колонки: 'Solvent' и '{sol_col}'")


Статистика по растворителям (Solvent):


count  n_unique   mean  median    std    min      max
Solvent                                                               
ethanol          10271     10125 1.1548  0.1087 4.7915 0.0000 173.2408
methanol          8220      8133 1.6771  0.1848 6.3175 0.0000 246.1129
isopropanol       7298      7192 0.7453  0.0669 4.1009 0.0000 217.5427
water             6814      6730 1.7767  0.0184 6.4268 0.0000 141.2494
ethyl acetate     6802      6743 1.0005  0.1431 3.1504 0.0000  65.2742
n-propanol        6616      6552 0.9170  0.1060 4.0987 0.0000 192.4017
acetone           6062      6017 1.6647  0.2478 5.3455 0.0000 126.7973
n-butanol         5613      5576 0.7942  0.0880 3.4211 0.0000 125.0804
acetonitrile      5251      5204 1.3097  0.1319 6.8883 0.0000 309.7926
DMF               2767      2756 1.8389  0.5496 3.0931 0.0000  43.4707
toluene           2618      2606 0.7557  0.0701 2.2804 0.0000  57.8925
isobutanol        2440      2429 0.8620  0.1072 3.7390 0.0000 102.2103
1,4-dioxane       2183      2181 1.1225  0.2625 2.9314 0.0001  71.1154
methyl acetate    1908      1904 1.1056  0.2544 3.0167 0.0000  80.2478
THF               1524      1523 2.5770  0.6439 6.8485 0.0000  92.3754
2-butanone        1464      1463 0.8411  0.1909 2.9176 0.0001  78.8927
n-pentanol        1374      1374 0.5269  0.0939 2.5819 0.0000  77.7626
sec-butanol       1210      1207 0.5659  0.0707 1.7223 0.0000  32.4740
n-hexane          1119      1115 0.3497  0.0044 2.2241 0.0000  44.9807
ethylene glycol   1103      1102 0.3301  0.0826 0.6161 0.0000   4.1747

In [93]:
if {"SMILES_Solute", sol_col}.issubset(df.columns):
    stats_by_solute = (
        df.groupby("SMILES_Solute")[sol_col]
        .agg(
            count="count",
            n_unique=lambda x: x.nunique(),
            mean="mean",
            median="median",
            std="std",
            min="min",
            max="max"
        )
        .sort_values("count", ascending=False)
    )

    print("Статистика по растворимым веществам (SMILES_Solute):")
    display(stats_by_solute.head(20))

else:
    print(f"Не найдены колонки: 'SMILES_Solute' и '{sol_col}'")

Статистика по растворимым веществам (SMILES_Solute):


count  n_unique   mean  \
SMILES_Solute                                                                
CN1CCN(C2=Nc3cc(Cl)ccc3Nc3ccccc32)CC1                 416       416 0.3763   
Cn1c(=O)c2c(ncn2CC2OCCO2)n(C)c1=O                     348       348 0.1349   
C[C@@H]1CC[C@@]2(OC1)O[C@H]1C[C@H]3[C@@H]4CC=C5...    339       339 0.0583   
CC(=O)Nc1ccc(OC(=O)c2ccccc2OC(C)=O)cc1                313       313 0.1078   
CC(C)C(=O)Nc1ccc([N+](=O)[O-])c(C(F)(F)F)c1           272       272 3.1715   
Nc1ccc(S(N)(=O)=O)cc1                                 267       267 0.2653   
O=c1[nH]cc(F)c(=O)[nH]1                               258       258 0.0420   
CN(C)CCC=C1c2ccccc2CCc2ccccc21.Cl                     248       248 0.7967   
Cc1c(C(=O)O)cccc1[N+](=O)[O-]                         244       244 0.6802   
Cc1nc2n(c(=O)c1CCN1CCC(c3noc4cc(F)ccc34)CC1)CCCC2     242       242 0.0496   
O=C(O)c1ccccc1                                        231       231 2.6807   
CS(=O)(=O)Nc1ccc([N+](=O)[O-])cc1Oc1ccccc1            230       230 0.1812   
Cc1ccc(S(N)(=O)=O)cc1                                 230       230 1.0626   
Cc1ccccc1S(N)(=O)=O                                   230       230 0.5881   
Cc1cc(C(=O)O)ccc1[N+](=O)[O-]                         224       224 0.4356   
On1nnc2ccccc21                                        221       221 0.4946   
c1ccc2c(c1)Cc1ccccc1-2                                221       221 0.9320   
COc1ccc(C(=O)O)cc1                                    220       220 0.1941   
O=C(O)CCCCC(=O)O                                      217       217 1.3355   
COC(=O)C(C)(C)N=NC(C)(C)C(=O)OC                       215       215 7.5639   

                                                    median    std    min  \
SMILES_Solute                                                              
CN1CCN(C2=Nc3cc(Cl)ccc3Nc3ccccc32)CC1               0.1874 0.4614 0.0336   
Cn1c(=O)c2c(ncn2CC2OCCO2)n(C)c1=O                   0.0909 0.1354 0.0051   
C[C@@H]1CC[C@@]2(OC1)O[C@H]1C[C@H]3[C@@H]4CC=C5...  0.0463 0.0493 0.0001   
CC(=O)Nc1ccc(OC(=O)c2ccccc2OC(C)=O)cc1              0.0151 0.2496 0.0000   
CC(C)C(=O)Nc1ccc([N+](=O)[O-])c(C(F)(F)F)c1         2.1862 3.0978 0.0000   
Nc1ccc(S(N)(=O)=O)cc1                               0.0362 0.4576 0.0000   
O=c1[nH]cc(F)c(=O)[nH]1                             0.0259 0.0437 0.0027   
CN(C)CCC=C1c2ccccc2CCc2ccccc21.Cl                   0.4706 1.1083 0.0078   
Cc1c(C(=O)O)cccc1[N+](=O)[O-]                       0.4741 0.7787 0.0847   
Cc1nc2n(c(=O)c1CCN1CCC(c3noc4cc(F)ccc34)CC1)CCCC2   0.0279 0.0613 0.0000   
O=C(O)c1ccccc1                                      2.1987 2.2710 0.0349   
CS(=O)(=O)Nc1ccc([N+](=O)[O-])cc1Oc1ccccc1          0.1223 0.2029 0.0005   
Cc1ccc(S(N)(=O)=O)cc1                               0.6920 0.9935 0.0484   
Cc1ccccc1S(N)(=O)=O                                 0.4080 0.5474 0.0226   
Cc1cc(C(=O)O)ccc1[N+](=O)[O-]                       0.2328 0.4596 0.0494   
On1nnc2ccccc21                                      0.2959 0.5291 0.0001   
c1ccc2c(c1)Cc1ccccc1-2                              0.6269 1.0069 0.0291   
COc1ccc(C(=O)O)cc1                                  0.1375 0.1997 0.0059   
O=C(O)CCCCC(=O)O                                    0.4923 1.9828 0.0004   
COC(=O)C(C)(C)N=NC(C)(C)C(=O)OC                     3.6758 9.1062 0.0622   

                                                       max  
SMILES_Solute                                               
CN1CCN(C2=Nc3cc(Cl)ccc3Nc3ccccc32)CC1               2.5678  
Cn1c(=O)c2c(ncn2CC2OCCO2)n(C)c1=O                   0.9432  
C[C@@H]1CC[C@@]2(OC1)O[C@H]1C[C@H]3[C@@H]4CC=C5...  0.4095  
CC(=O)Nc1ccc(OC(=O)c2ccccc2OC(C)=O)cc1              1.5257  
CC(C)C(=O)Nc1ccc([N+](=O)[O-])c(C(F)(F)F)c1        14.3742  
Nc1ccc(S(N)(=O)=O)cc1                               1.8869  
O=c1[nH]cc(F)c(=O)[nH]1                             0.2207  
CN(C)CCC=C1c2ccccc2CCc2ccccc21.Cl                   6.1973  
Cc1c(C(=O)O)cccc1[N+](=O)[O-]                       

### Выводы

1. Данные чистые без повторов, однако есть повторы в рамках тройки Solvent-Solubility, связанный с тем, что растворимость различная при различных температурах
2. Количество выбросов по температуре и LogS достаточно адекватное, так что при обучении предсказательной модели LogS их можно и отбросить
3. Несмотря на то, что Solubility(mole_fraction), Solubility(mol/L), LogS(mol/L) отражают одну и ту же величину, нормально распределена LogS, так что выберем её как таргет